In [126]:
# Install PyTorch and necessary libraries
# Use the official PyTorch install command for Colab with CUDA support
!pip install -q torch torchvision torchaudio --index-url https://download.pytorch.org/whl/cu118
# Confirm the installation
!pip install -q git+https://github.com/IntelLabs/bayesian-torch.git

!pip show torch
!pip show torchvision
print("!!!!!!!!")
!pip show bayesian-torch



[notice] A new release of pip is available: 24.2 -> 24.3.1
[notice] To update, run: pip install --upgrade pip

[notice] A new release of pip is available: 24.2 -> 24.3.1
[notice] To update, run: pip install --upgrade pip
Name: torch
Version: 2.5.1
Summary: Tensors and Dynamic neural networks in Python with strong GPU acceleration
Home-page: https://pytorch.org/
Author: PyTorch Team
Author-email: packages@pytorch.org
License: BSD-3-Clause
Location: /home/prashant/venv/dd2412/lib/python3.12/site-packages
Requires: filelock, fsspec, jinja2, networkx, nvidia-cublas-cu12, nvidia-cuda-cupti-cu12, nvidia-cuda-nvrtc-cu12, nvidia-cuda-runtime-cu12, nvidia-cudnn-cu12, nvidia-cufft-cu12, nvidia-curand-cu12, nvidia-cusolver-cu12, nvidia-cusparse-cu12, nvidia-nccl-cu12, nvidia-nvjitlink-cu12, nvidia-nvtx-cu12, setuptools, sympy, triton, typing-extensions
Required-by: bayesian-torch, torchaudio, torchvision
Name: torchvision
Version: 0.20.1
Summary: image and video datasets and models for torch dee

In [208]:
import torch
import torchvision
import torchvision.transforms as transforms
import random
from torch.utils.data import random_split
from torch.utils.data import Dataset, DataLoader, Subset
import numpy as np
from sklearn.model_selection import KFold
import torch.nn as nn
from copy import deepcopy

import torch.nn.functional as F
import torch.optim as optim
from torch.utils.data import DataLoader
from torch.distributions.normal import Normal
# from bayesian_torch.utils.losses import kl_divergence_from_nn
from bayesian_torch.layers import Conv2dReparameterization, LinearReparameterization


# Check if CUDA is available and set the device
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
print(f"Using device: {device}")

# No explicit eager execution toggle is required in PyTorch, as it works in an imperative manner by default.

# Seed for reproducibility (if needed)
torch.manual_seed(42)
np.random.seed(42)
random.seed(42)
if torch.cuda.is_available():
    torch.cuda.manual_seed_all(42)
    torch.cuda.manual_seed(42)
    

# PyTorch distributions equivalent to TensorFlow Probability
from torch.distributions import constraints
from torch.distributions import Distribution, Normal, Bernoulli, Categorical

# Example to verify PyTorch distributions:
# Normal distribution example (equivalent to TensorFlow Probability's `tfd.Normal`)
example_dist = Normal(loc=0.0, scale=1.0)
print(f"Sample from Normal(0, 1): {example_dist.sample()}")

Using device: cuda
Sample from Normal(0, 1): 0.33669036626815796


In [171]:
from torch.utils.data import DataLoader

# Define transformations for the dataset
transform = transforms.Compose([
    transforms.ToTensor(),  # Convert images to PyTorch tensors
])

# Load CIFAR-100 dataset
cifar100_train = torchvision.datasets.CIFAR100(root='./data', train=True, download=True, transform=transform)
cifar100_test = torchvision.datasets.CIFAR100(root='./data', train=False, download=True, transform=transform)

# Combine training and test datasets
from torch.utils.data import ConcatDataset
cifar100_all = ConcatDataset([cifar100_train, cifar100_test])

# Print dataset sizes
total_samples = len(cifar100_train) + len(cifar100_test)
print(f"CIFAR-100 Total Samples: {total_samples}")

# Print the structure of CIFAR-100 dataset
print("\nCIFAR-100 Dataset Sample:")
data_loader = DataLoader(cifar100_all, batch_size=1, shuffle=True)
for sample in data_loader:
    images, labels = sample  # Each sample includes images and labels
    print(f"Image shape: {images.shape}, Label: {labels}")
    break  # Just one sample

# Extract fine and coarse labels from CIFAR-100 dataset
# Fine labels are directly the class labels in torchvision's CIFAR-100 dataset
fine_labels = cifar100_train.classes  # List of fine labels
print("\nCIFAR-100 Fine Labels:")
print(fine_labels)

# Coarse labels (superclass labels) need a mapping since PyTorch CIFAR-100 doesn't provide them directly.
# You can manually map them if needed, based on CIFAR-100 hierarchy.
# For simplicity, here we'll define them manually if required in future steps.


Files already downloaded and verified
Files already downloaded and verified
CIFAR-100 Total Samples: 60000

CIFAR-100 Dataset Sample:
Image shape: torch.Size([1, 3, 32, 32]), Label: tensor([87])

CIFAR-100 Fine Labels:
['apple', 'aquarium_fish', 'baby', 'bear', 'beaver', 'bed', 'bee', 'beetle', 'bicycle', 'bottle', 'bowl', 'boy', 'bridge', 'bus', 'butterfly', 'camel', 'can', 'castle', 'caterpillar', 'cattle', 'chair', 'chimpanzee', 'clock', 'cloud', 'cockroach', 'couch', 'crab', 'crocodile', 'cup', 'dinosaur', 'dolphin', 'elephant', 'flatfish', 'forest', 'fox', 'girl', 'hamster', 'house', 'kangaroo', 'keyboard', 'lamp', 'lawn_mower', 'leopard', 'lion', 'lizard', 'lobster', 'man', 'maple_tree', 'motorcycle', 'mountain', 'mouse', 'mushroom', 'oak_tree', 'orange', 'orchid', 'otter', 'palm_tree', 'pear', 'pickup_truck', 'pine_tree', 'plain', 'plate', 'poppy', 'porcupine', 'possum', 'rabbit', 'raccoon', 'ray', 'road', 'rocket', 'rose', 'sea', 'seal', 'shark', 'shrew', 'skunk', 'skyscraper',

In [172]:
# Define fine and coarse labels as lists
fine_labels = [
    'apple', 'aquarium_fish', 'baby', 'bear', 'beaver', 'bed', 'bee', 'beetle', 'bicycle', 'bottle',
    'bowl', 'boy', 'bridge', 'bus', 'butterfly', 'camel', 'can', 'castle', 'caterpillar', 'cattle',
    'chair', 'chimpanzee', 'clock', 'cloud', 'cockroach', 'couch', 'crab', 'crocodile', 'cup', 'dinosaur',
    'dolphin', 'elephant', 'flatfish', 'forest', 'fox', 'girl', 'hamster', 'house', 'kangaroo', 'keyboard',
    'lamp', 'lawn_mower', 'leopard', 'lion', 'lizard', 'lobster', 'man', 'maple_tree', 'motorcycle', 'mountain',
    'mouse', 'mushroom', 'oak_tree', 'orange', 'orchid', 'otter', 'palm_tree', 'pear', 'pickup_truck', 'pine_tree',
    'plain', 'plate', 'poppy', 'porcupine', 'possum', 'rabbit', 'raccoon', 'ray', 'road', 'rocket',
    'rose', 'sea', 'seal', 'shark', 'shrew', 'skunk', 'skyscraper', 'snail', 'snake', 'spider',
    'squirrel', 'streetcar', 'sunflower', 'sweet_pepper', 'table', 'tank', 'telephone', 'television', 'tiger', 'tractor',
    'train', 'trout', 'tulip', 'turtle', 'wardrobe', 'whale', 'willow_tree', 'wolf', 'woman', 'worm'
]

fine_labels_string = fine_labels
fine_labels_string.append('wrong group')

coarse_labels = [
    'aquatic_mammals', 'fish', 'flowers', 'food_containers', 'fruit_and_vegetables',
    'household_electrical_devices', 'household_furniture', 'insects', 'large_carnivores', 'large_man-made_outdoor_things',
    'large_natural_outdoor_scenes', 'large_omnivores_and_herbivores', 'medium_mammals', 'non-insect_invertebrates',
    'people', 'reptiles', 'small_mammals', 'trees', 'vehicles_1', 'vehicles_2'
]

# Coarse-to-Fine Mapping (as a dictionary of indices)
coarse_to_fine_mapping = {
    coarse_labels.index('aquatic_mammals'): [fine_labels.index(label) for label in ['beaver', 'dolphin', 'otter', 'seal', 'whale']],
    coarse_labels.index('fish'): [fine_labels.index(label) for label in ['aquarium_fish', 'flatfish', 'ray', 'shark', 'trout']],
    coarse_labels.index('flowers'): [fine_labels.index(label) for label in ['orchid', 'poppy', 'rose', 'sunflower', 'tulip']],
    coarse_labels.index('food_containers'): [fine_labels.index(label) for label in ['bottle', 'bowl', 'can', 'cup', 'plate']],
    coarse_labels.index('fruit_and_vegetables'): [fine_labels.index(label) for label in ['apple', 'mushroom', 'orange', 'pear', 'sweet_pepper']],
    coarse_labels.index('household_electrical_devices'): [fine_labels.index(label) for label in ['clock', 'keyboard', 'lamp', 'telephone', 'television']],
    coarse_labels.index('household_furniture'): [fine_labels.index(label) for label in ['bed', 'chair', 'couch', 'table', 'wardrobe']],
    coarse_labels.index('insects'): [fine_labels.index(label) for label in ['bee', 'beetle', 'butterfly', 'caterpillar', 'cockroach']],
    coarse_labels.index('large_carnivores'): [fine_labels.index(label) for label in ['bear', 'leopard', 'lion', 'tiger', 'wolf']],
    coarse_labels.index('large_man-made_outdoor_things'): [fine_labels.index(label) for label in ['bridge', 'castle', 'house', 'road', 'skyscraper']],
    coarse_labels.index('large_natural_outdoor_scenes'): [fine_labels.index(label) for label in ['cloud', 'forest', 'mountain', 'plain', 'sea']],
    coarse_labels.index('large_omnivores_and_herbivores'): [fine_labels.index(label) for label in ['camel', 'cattle', 'chimpanzee', 'elephant', 'kangaroo']],
    coarse_labels.index('medium_mammals'): [fine_labels.index(label) for label in ['fox', 'porcupine', 'possum', 'raccoon', 'skunk']],
    coarse_labels.index('non-insect_invertebrates'): [fine_labels.index(label) for label in ['crab', 'lobster', 'snail', 'spider', 'worm']],
    coarse_labels.index('people'): [fine_labels.index(label) for label in ['baby', 'boy', 'girl', 'man', 'woman']],
    coarse_labels.index('reptiles'): [fine_labels.index(label) for label in ['crocodile', 'dinosaur', 'lizard', 'snake', 'turtle']],
    coarse_labels.index('small_mammals'): [fine_labels.index(label) for label in ['hamster', 'mouse', 'rabbit', 'shrew', 'squirrel']],
    coarse_labels.index('trees'): [fine_labels.index(label) for label in ['maple_tree', 'oak_tree', 'palm_tree', 'pine_tree', 'willow_tree']],
    coarse_labels.index('vehicles_1'): [fine_labels.index(label) for label in ['bicycle', 'bus', 'motorcycle', 'pickup_truck', 'train']],
    coarse_labels.index('vehicles_2'): [fine_labels.index(label) for label in ['lawn_mower', 'rocket', 'streetcar', 'tank', 'tractor']]
}

# Fine-to-Coarse Mapping (as a dictionary of indices)
fine_to_coarse_mapping = {}
for coarse_idx, fine_indices in coarse_to_fine_mapping.items():
    for fine_idx in fine_indices:
        fine_to_coarse_mapping[fine_idx] = coarse_idx

# # Print example mappings
# print("\nCoarse-to-Fine Mapping (Indices):")
# for coarse_idx, fine_indices in coarse_to_fine_mapping.items():
#     print(f"Coarse Label {coarse_labels[coarse_idx]} -> Fine Indices: {fine_indices}")

# print("\nFine-to-Coarse Mapping (Indices):")
# for fine_idx, coarse_idx in fine_to_coarse_mapping.items():
#     print(f"Fine Label {fine_labels[fine_idx]} -> Coarse Label {coarse_labels[coarse_idx]}")


In [173]:
print(coarse_to_fine_mapping.keys())

dict_keys([0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19])


In [174]:
# Print CIFAR-100 fine labels
print("\nCIFAR-100 Fine Labels:")
print(fine_labels)  # Already defined as a list of fine labels

# Print CIFAR-100 coarse labels
print("\nCIFAR-100 Coarse Labels:")
print(coarse_labels)  # Already defined as a list of coarse labels



CIFAR-100 Fine Labels:
['apple', 'aquarium_fish', 'baby', 'bear', 'beaver', 'bed', 'bee', 'beetle', 'bicycle', 'bottle', 'bowl', 'boy', 'bridge', 'bus', 'butterfly', 'camel', 'can', 'castle', 'caterpillar', 'cattle', 'chair', 'chimpanzee', 'clock', 'cloud', 'cockroach', 'couch', 'crab', 'crocodile', 'cup', 'dinosaur', 'dolphin', 'elephant', 'flatfish', 'forest', 'fox', 'girl', 'hamster', 'house', 'kangaroo', 'keyboard', 'lamp', 'lawn_mower', 'leopard', 'lion', 'lizard', 'lobster', 'man', 'maple_tree', 'motorcycle', 'mountain', 'mouse', 'mushroom', 'oak_tree', 'orange', 'orchid', 'otter', 'palm_tree', 'pear', 'pickup_truck', 'pine_tree', 'plain', 'plate', 'poppy', 'porcupine', 'possum', 'rabbit', 'raccoon', 'ray', 'road', 'rocket', 'rose', 'sea', 'seal', 'shark', 'shrew', 'skunk', 'skyscraper', 'snail', 'snake', 'spider', 'squirrel', 'streetcar', 'sunflower', 'sweet_pepper', 'table', 'tank', 'telephone', 'television', 'tiger', 'tractor', 'train', 'trout', 'tulip', 'turtle', 'wardrobe',

In [175]:


def preprocess_data(data):
    """
    Preprocess the image and optionally return coarse labels.

    Args:
        data: A tuple containing (image, fine_label). Coarse labels are handled externally.
        use_coarse: If True, also return coarse labels.

    Returns:
        Processed image, fine label, and optionally coarse label.
    """
    transform = transforms.Compose([
        # transforms.RandomCrop(32, padding=4),  # Random crop with padding
        # transforms.RandomHorizontalFlip(),  # Random horizontal flip
        transforms.Normalize(mean=(0.5, 0.5, 0.44), std=(0.26, 0.25, 0.27))  # CIFAR-100 normalization
    ])

    image, fine_label = data  # Unpack the tuple
    # image = image / 255.0  # Normalize image to [0, 1] range
    image = transform(image)  # Apply the normalization transform

    return image, fine_label

In [176]:
# Transform dataset in-place with a list comprehension
cifar100_coarse_dataset = [
    preprocess_data(data) for data in cifar100_all
]

label_dictionary = {}
for sample in cifar100_coarse_dataset:
    coarse_lbl = fine_to_coarse_mapping[sample[1]]
    label_dictionary[sample[0]] = {'coarse_label':coarse_lbl, 'fine_label':sample[1], 'original_coarse':coarse_lbl, 'original_fine':sample[1], 'last_predicted':-1, 'last_predicted_count':0, 'should_flip':0}


# Create DataLoader for the preprocessed dataset
# coarse_dataloader = DataLoader(cifar100_coarse_dataset, batch_size=32, shuffle=True)

# # Iterate through the DataLoader
# for images, coarse_labels, fine_labels, orig_coarse, orig_fine in coarse_dataloader:
#     print(f"Images shape: {images.shape}")
#     print(f"Coarse labels: {coarse_labels}")
#     print(f"Fine labels: {fine_labels}")
#     print(f"Original coarse labels: {orig_coarse}")
#     print(f"Original fine labels: {orig_fine}")
#     break

# for images, coarse_labels, fine_labels, orig_coarse, orig_fine in cifar100_coarse_dataset:
#     print(f"Images shape: {images.shape}")
#     print(f"Coarse labels: {coarse_labels}")
#     print(f"Fine labels: {fine_labels}")
#     print(f"Original coarse labels: {orig_coarse}")
#     print(f"Original fine labels: {orig_fine}")
#     break

In [253]:
def get_fine_datasets_and_mappings(dataset, coarse_labels, mapping=None, no_match=1/6):
    """
    Create fine-grained datasets and mappings for each coarse label in PyTorch.

    Args:
        dataset: The dataset object (e.g., CIFAR-100).
        coarse_labels: List of coarse label names.
        no_match: Proportion of out-of-group samples to include.

    Returns:
        fine_datasets: A dictionary where keys are coarse label indices and values are filtered datasets.
        coarse_fine_local_mapping: A dictionary mapping coarse label indices to fine-to-coarse label mappings.
    """
    fine_datasets = {}
    coarse_fine_local_mapping = {}

    # Iterate over each coarse label
    for coarse_label in list(coarse_to_fine_mapping.keys()):
        # print("Coarse idx: ",coarse_label)
        
        # print(len(dataset))
        # Filter the dataset for the current coarse label
        coarse_data = [sample for sample in dataset if label_dictionary[sample[0]]['coarse_label'] == coarse_label]
        
        # print(len(coarse_data))
        
        # Initialize the mapping and dataset
        label_counter = 1
        coarse_fine_local_mapping[coarse_label] = {}
        coarse_fine_local_mapping[coarse_label][-1] = 0
        fine_datasets[coarse_label] = coarse_data

        
        # all_coarse_data = [sample for sample in label_dictionary.keys() if label_dictionary[sample]['coarse_label'] == coarse_label]

        # Identify unique fine labels for the current coarse label
        # unique_labels2 = set(sample[1] for sample in coarse_data)
        unique_labels = set(label_dictionary[sample[0]]['fine_label'] for sample in coarse_data)
        # print("Unique labels:", unique_labels)
        # print("Unique labels2:", unique_labels2)
        # Create fine-to-coarse local mapping
        for fine_label in unique_labels:
            coarse_fine_local_mapping[coarse_label][int(fine_label)] = label_counter
            label_counter += 1
        # print("Coarse fine local mapping:", coarse_fine_local_mapping[coarse_label])


        # Add the no_match portion of the dataset
        no_match_data = [sample for sample in dataset if fine_to_coarse_mapping[sample[1]] != coarse_label]
        no_match_count = int(len(fine_datasets[coarse_label]) * no_match)
        # print("No match count:", no_match_count)

        # Shuffle and take the required number of no_match samples
        random.shuffle(no_match_data)
        no_match_data = no_match_data[:no_match_count]

        # Mark no_match samples with a fine label of -1
        # no_match_data = [(data[0], data[1], -1, data[3], data[4]) for data in no_match_data]
        no_match_data = [(data[0], -1) for data in no_match_data]

        # Concatenate the no_match samples with the original coarse data
        fine_datasets[coarse_label] = fine_datasets[coarse_label] + no_match_data

        # print("POST CONCATENATION:")
        # print("Dataset size:", len(fine_datasets[coarse_label]))
        # print("Unique fine labels:", set(sample[2] for sample in fine_datasets[coarse_label]))


        # Replace fine labels with local mappings
        mapped_dataset = []
        for sample in fine_datasets[coarse_label]:
            data, fine = sample
            if mapping is None:
                mapped_fine = coarse_fine_local_mapping[coarse_label][fine]
            else:
                mapped_fine = mapping[coarse_label][fine]
            mapped_dataset.append((data, mapped_fine))
        fine_datasets[coarse_label] = mapped_dataset

        # print("Unique fine labels post-mapping:", set(sample[2] for sample in fine_datasets[coarse_label]))
        # print(coarse_to_fine_mapping[coarse_label])
    return fine_datasets, coarse_fine_local_mapping

In [178]:

def get_train_test(dataset, train_split=0.8):
    """
    Split the dataset into training and testing subsets.

    Args:
        dataset: A PyTorch Dataset object.
        train_split: Fraction of the dataset to include in the training set.

    Returns:
        train_dataset: Training subset of the dataset.
        test_dataset: Testing subset of the dataset.
    """
    size = len(dataset)  # Total size of the dataset
    train_size = int(train_split * size)  # Calculate training size
    test_size = size - train_size  # Calculate test size

    # Split the dataset
    train_dataset, test_dataset = random_split(dataset, [train_size, test_size])
    return train_dataset, test_dataset


In [179]:
# for sample in cifar100_coarse_dataset:
#     print(sample[0].shape, sample[1], sample[2], sample[3], sample[4])
    # break



# Split the coarse dataset into training and testing subsets
coarse_train, coarse_test = get_train_test(cifar100_coarse_dataset)
# Map coarse_train to retain only (data, coarse) tuples
coarse_train = [(data, fine_to_coarse_mapping[fine]) for data, fine in coarse_train]
coarse_test = [(data, fine_to_coarse_mapping[fine]) for data, fine in coarse_test]


fine_datasets, coarse_fine_local_mapping = get_fine_datasets_and_mappings(cifar100_coarse_dataset, coarse_labels)

fine_training_datasets = {}
fine_testing_datasets = {}


#### !!!!! ####
# cifar100_coarse_dataset = [(sample[0], sample[1], sample[2]) for sample in cifar100_coarse_dataset]



for coarse_label in coarse_to_fine_mapping.keys():
    # Split fine-grained dataset for this coarse label
    fine_train, fine_test = get_train_test(fine_datasets[coarse_label])

    # Modify fine_train to include other relevant labels without breaking the structure
    fine_training_datasets[coarse_label] = [
        (data, fine) for data, fine in fine_train
    ]

    # Store the testing dataset
    fine_testing_datasets[coarse_label] = [
        (data, fine) for data, fine in fine_test
    ]

    print(f"Coarse Label: {coarse_label}")
    print(f"Fine Training Dataset Size: {len(fine_training_datasets[coarse_label])}")


print()
print("LABEL DICTIONARY:",label_dictionary[cifar100_coarse_dataset[0][0]]['coarse_label'])


Coarse Label: 0
Fine Training Dataset Size: 2800
Coarse Label: 1
Fine Training Dataset Size: 2800
Coarse Label: 2
Fine Training Dataset Size: 2800
Coarse Label: 3
Fine Training Dataset Size: 2800
Coarse Label: 4
Fine Training Dataset Size: 2800
Coarse Label: 5
Fine Training Dataset Size: 2800
Coarse Label: 6
Fine Training Dataset Size: 2800
Coarse Label: 7
Fine Training Dataset Size: 2800
Coarse Label: 8
Fine Training Dataset Size: 2800
Coarse Label: 9
Fine Training Dataset Size: 2800
Coarse Label: 10
Fine Training Dataset Size: 2800
Coarse Label: 11
Fine Training Dataset Size: 2800
Coarse Label: 12
Fine Training Dataset Size: 2800
Coarse Label: 13
Fine Training Dataset Size: 2800
Coarse Label: 14
Fine Training Dataset Size: 2800
Coarse Label: 15
Fine Training Dataset Size: 2800
Coarse Label: 16
Fine Training Dataset Size: 2800
Coarse Label: 17
Fine Training Dataset Size: 2800
Coarse Label: 18
Fine Training Dataset Size: 2800
Coarse Label: 19
Fine Training Dataset Size: 2800

LABEL DIC

In [181]:
def compute_kl_divergence(model):
    """
    Compute the KL divergence for all Bayesian layers in the model.

    Args:
        model: A PyTorch model with Bayesian layers.

    Returns:
        Total KL divergence across all Bayesian layers.
    """
    kl_divergence = 0.0
    for layer in model.modules():
        if hasattr(layer, 'kl_loss'):
            kl_divergence += layer.kl_loss()
    return kl_divergence




In [182]:
class BayesianModel(nn.Module):
    def __init__(self, num_classes):
        super(BayesianModel, self).__init__()
        # Bayesian Convolutional Layers
        self.conv1 = Conv2dReparameterization(3, 32, kernel_size=3, stride=1, padding=1)
        self.conv2 = Conv2dReparameterization(32, 64, kernel_size=3, stride=1, padding=1)
        # Pooling
        self.pool = nn.MaxPool2d(kernel_size=(2, 2))
        # Flatten
        self.flatten = nn.Flatten()
        # Bayesian Dense Layers
        self.fc1 = LinearReparameterization(64 * 8 * 8, 128)
        self.fc2 = LinearReparameterization(128, num_classes)


        # for name, param in self.named_parameters():
        #   if 'rho' in name:
        #       nn.init.normal_(param, mean=-1.0, std=0.2)  # Smaller variance for rho
        #   elif 'mu' in name:
        #       nn.init.normal_(param, mean=0.0, std=0.5)

    def forward(self, x):
        # Convolutional Layers with Pooling
        x, _ = self.conv1(x)  # Extract only the output Tensor
        x = torch.relu(x)
        x = self.pool(x)
        x, _ = self.conv2(x)  # Extract only the output Tensor
        x = torch.relu(x)
        x = self.pool(x)
        # Fully Connected Layers
        x = self.flatten(x)
        x, _ = self.fc1(x)  # Extract only the output Tensor
        x = torch.relu(x)
        x, _ = self.fc2(x)  # Extract only the output Tensor
        # x = torch.softmax(x, dim=1)  # Output layer with softmax
        return x

class SmallBayesianModel(nn.Module):
    def __init__(self, num_classes):
        super(SmallBayesianModel, self).__init__()
        # Bayesian Convolutional Layers
        self.conv1 = Conv2dReparameterization(3, 32, kernel_size=3, stride=1, padding=1)
        self.conv2 = Conv2dReparameterization(32, 64, kernel_size=3, stride=1, padding=1)

        # Pooling
        self.pool = nn.MaxPool2d(kernel_size=(2, 2))

        # Flatten
        self.flatten = nn.Flatten()

        # Bayesian Dense Layers
        self.fc1 = LinearReparameterization(64 * 8 * 8, num_classes)


        # for name, param in self.named_parameters():
        #   if 'rho' in name:
        #       nn.init.normal_(param, mean=-1.0, std=0.2)  # Smaller variance for rho
        #   elif 'mu' in name:
        #       nn.init.normal_(param, mean=0.0, std=0.5)


    def forward(self, x):
        # Convolutional Layers with Pooling
        x, _ = self.conv1(x)  # Extract only the output Tensor
        x = torch.relu(x)
        x = self.pool(x)

        x, _ = self.conv2(x)  # Extract only the output Tensor
        x = torch.relu(x)
        x = self.pool(x)

        # Fully Connected Layers
        x = self.flatten(x)
        x, _ = self.fc1(x)  # Extract only the output Tensor
        # x = torch.softmax(x, dim=1)

        return x


# model = SmallBayesianModel(10)
# dummy_input = torch.randn(8, 3, 32, 32)  # Dummy batch
# output = model(dummy_input)
# print("Output shape:", output.shape)


# print("LABEL DICTIONARY:",label_dictionary[cifar100_coarse_dataset[0][0]]['coarse_label'])


In [183]:
# Define a function for evaluating a model
def evaluate_model(model, criterion, test_dataset, batch_size=100):
    dataloader = DataLoader(test_dataset, batch_size=batch_size, shuffle=False)  # Create DataLoader
    model.eval()  # Set model to evaluation mode

    total_loss = 0.0
    correct = 0
    total = 0

    with torch.no_grad():  # Disable gradient computation
        for inputs, labels in dataloader:
            inputs, labels = inputs.to(device), labels.to(device)  # Move data to the correct device

            # Forward pass
            outputs = model(inputs)
            loss = criterion(outputs, labels)
            total_loss += loss.item()

            # Compute accuracy
            _, predicted = torch.max(outputs, 1)
            correct += (predicted == labels).sum().item()
            total += labels.size(0)

    # Calculate average loss and accuracy
    avg_loss = total_loss / len(dataloader)
    accuracy = 100 * correct / total

    print(f"Test Loss: {avg_loss:.4f}, Test Accuracy: {accuracy:.2f}%")
    return avg_loss, accuracy

# Evaluate models for coarse labels 1 and 2
# print("MODEL 1")
# evaluate_model(fine_models[1]['model'], fine_models[1]['loss_fn'], fine_testing_datasets[1], batch_size=100)
# print("MODEL 5")
# evaluate_model(fine_models[5]['model'], fine_models[2]['loss_fn'], fine_testing_datasets[1], batch_size=100)



In [184]:
def train_model_with_kl(model, train_loader, optimizer, criterion, kl_weight, epochs, test_loaded=None, is_fine=False):
    """
    Train a Bayesian PyTorch model with KL loss on the given dataset.

    Args:
        model: The PyTorch Bayesian model to train.
        train_loader: DataLoader for the training dataset.
        optimizer: Optimizer for updating model weights.
        criterion: Loss function (e.g., CrossEntropyLoss).
        kl_weight: Weight for the KL loss term.
        epochs: Number of training epochs.
    """
    model.to(device)  # Move the model to the appropriate device
    model.train()  # Set the model to training mode

    losses = []
    accuracies = []
    for epoch in range(epochs):
        running_loss = 0.0
        correct = 0
        total = 0

        # kl_weight = max(0.01, kl_weight * (epoch / epochs))  # Gradually increase KL weight
        kl_weight = 0.001
        best_acc = 0
        for batch_idx, (data, labels) in enumerate(train_loader):
            # Move data and labels to the appropriate device (GPU or CPU)
            data, labels = data.to(device), labels.to(device)

            # Forward pass
            optimizer.zero_grad()
            outputs = model(data)

            # Compute the classification loss
            ce_loss = criterion(outputs, labels)

            # Compute the KL divergence
            kl_loss = compute_kl_divergence(model)

            # Combine the losses
            total_loss = ce_loss + kl_weight * kl_loss
            running_loss += total_loss.item()
            
            # Backward pass and optimize
            total_loss.backward()
            torch.nn.utils.clip_grad_norm_(model.parameters(), max_norm=1.0)
            optimizer.step()

            # Accuracy calculation
            _, predicted = torch.max(outputs, 1)
            total += labels.size(0)
            correct += (predicted == labels).sum().item()

            # print("kl_loss: ", kl_loss)
            layer = model.conv1
            # print("Prior mean:", layer.weight_mu.mean())
            # print("Posterior stddev:", torch.nn.functional.softplus(layer.weight_rho).mean())

            if test_loaded is not None:
                test_loss, test_accuracy = evaluate_model(model, criterion, test_loaded, batch_size=64)
                if best_acc == 0:
                    best_acc = test_accuracy
                else:
                    if test_accuracy > best_acc:
                        break



        # Print epoch stats
        epoch_loss = running_loss / len(train_loader)
        accuracy = correct / total * 100
        losses.append(epoch_loss)
        accuracies.append(accuracy)
        # print(f"Epoch {epoch + 1}: CE Loss = {ce_loss.item():.4f}, KL Loss = {kl_loss.item():.4f}")
        if not is_fine:
            print(f"Epoch {epoch + 1}/{epochs}, Loss: {epoch_loss:.4f}, Accuracy: {accuracy:.2f}%")
        # for name, param in model.named_parameters():
        #     if 'mu' in name or 'rho' in name:
        #         print(f"{name}: Mean = {param.mean().item()}, Std = {param.std().item()}")
    return losses, accuracies



In [186]:
# Training with 0 noise
# Define DataLoader for batching
BATCH_SIZE = 128
EPOCHS = 1
kl_weight = 0.001
train_loader = DataLoader(coarse_train, batch_size=BATCH_SIZE, shuffle=True)


# Create the Bayesian model for coarse classification
model_cifar100_coarse = BayesianModel(num_classes=20)  # 20 coarse classes

# Define optimizer and loss function for the coarse model
coarse_optimizer = optim.Adam(model_cifar100_coarse.parameters(), lr=0.001)#, weight_decay=0.0004)
coarse_loss_fn = nn.CrossEntropyLoss()  # Similar to sparse_categorical_crossentropy in TensorFlow

coarse_model = {
    'model': model_cifar100_coarse,
    'optimizer': coarse_optimizer,
    'loss_fn': coarse_loss_fn
}

# DEBUGGING CODE!!
# dummy_input = torch.randn(BATCH_SIZE, 3, 32, 32).requires_grad_(True)  # Enable gradient tracking
# output = coarse_model['model'](dummy_input)
# output.sum().backward()  # Compute gradients

# for name, param in coarse_model['model'].named_parameters():
#     if param.grad is not None:
#         print(f"{name} gradient mean: {param.grad.mean()}")
#     else:
#         print(f"{name} has no gradient")

# # Pass dummy_input through the entire model before testing individual layers
# x = dummy_input
# counter = 0


# for layer in [coarse_model['model'].conv1, coarse_model['model'].conv2]:
#     if isinstance(layer, nn.Module):
#         x, _ = layer(x)  # Ensure the input is correctly shaped for the layer
#         grads = torch.autograd.grad(outputs=x.sum(), inputs=layer.parameters(), retain_graph=True)
#         print(f"Layer {layer}: Gradients = {[g.mean().item() for g in grads if g is not None]}")

# batch_size = 8  # Example batch size
# flattened_size = 4096  # Example flattened size (64 * 8 * 8)

# # Generate dummy input for fc1
# fc1_input = torch.randn(batch_size, flattened_size)
# x = fc1_input
# for layer in [coarse_model['model'].fc1, coarse_model['model'].fc2]:
#     if isinstance(layer, nn.Module):
#         x, _ = layer(x)  # Ensure the input is correctly shaped for the layer
#         grads = torch.autograd.grad(outputs=x.sum(), inputs=layer.parameters(), retain_graph=True)
#         print(f"Layer {layer}: Gradients = {[g.mean().item() for g in grads if g is not None]}")



train_model_with_kl(coarse_model['model'], train_loader, coarse_model['optimizer'], coarse_model['loss_fn'], kl_weight, EPOCHS, is_fine=False)

print("EVALUATING COARSE MODEL")
evaluate_model(coarse_model['model'], coarse_model['loss_fn'], coarse_test, batch_size=100)



Epoch 1/1, Loss: 2.8847, Accuracy: 14.14%
EVALUATING COARSE MODEL
Test Loss: 2.6064, Test Accuracy: 19.57%


(2.606405435005824, 19.575)

In [187]:

fine_models = {}

for coarse_label, fine_labels in coarse_to_fine_mapping.items():

    # Number of classes for this fine-grained model (including the no_match class)
    no_classes = len(fine_labels) + 1  # Add 1 for the no_match label

    # Create a small Bayesian model for fine-grained classification
    fine_model = SmallBayesianModel(num_classes=no_classes)  # Replace with a smaller architecture if needed
    fine_model.train()
    # Define optimizer and loss function for the fine-grained model
    fine_optimizer = optim.Adam(fine_model.parameters(), lr=0.001)
    fine_loss_fn = nn.CrossEntropyLoss()

    fine_models[coarse_label] = {
        'model': fine_model,
        'optimizer': fine_optimizer,
        'loss_fn': fine_loss_fn
    }


# print("LABEL DICTIONARY:",label_dictionary[cifar100_coarse_dataset[0][0]]['coarse_label'])


print(fine_models[0])

EPOCHS = 1
kl_weight = 0.001
for coarse_label, fine_labels in coarse_to_fine_mapping.items():
    print("Coarse label: ", coarse_label)
    # BATCH_SIZE = len(fine_training_datasets[coarse_label])
    BATCH_SIZE = 64
    if BATCH_SIZE < 10:
        BATCH_SIZE = 10
    print("Batch size: ", BATCH_SIZE)

    fine_dataset_local = DataLoader(fine_training_datasets[coarse_label], batch_size=BATCH_SIZE, shuffle=True)
    fine_model = fine_models[coarse_label]

    train_model_with_kl(fine_model['model'], fine_dataset_local, fine_model['optimizer'], fine_model['loss_fn'], kl_weight, EPOCHS)
    print("EVALUATING FINE MODEL")
    evaluate_model(fine_model['model'], fine_model['loss_fn'], fine_testing_datasets[coarse_label], batch_size=64)


# print("LABEL DICTIONARY:",label_dictionary[cifar100_coarse_dataset[0][0]]['coarse_label'])



{'model': SmallBayesianModel(
  (conv1): Conv2dReparameterization()
  (conv2): Conv2dReparameterization()
  (pool): MaxPool2d(kernel_size=(2, 2), stride=(2, 2), padding=0, dilation=1, ceil_mode=False)
  (flatten): Flatten(start_dim=1, end_dim=-1)
  (fc1): LinearReparameterization()
), 'optimizer': Adam (
Parameter Group 0
    amsgrad: False
    betas: (0.9, 0.999)
    capturable: False
    differentiable: False
    eps: 1e-08
    foreach: None
    fused: None
    lr: 0.001
    maximize: False
    weight_decay: 0
), 'loss_fn': CrossEntropyLoss()}
Coarse label:  0
Batch size:  64
Epoch 1/1, Loss: 3.3955, Accuracy: 24.39%
EVALUATING FINE MODEL
Test Loss: 2.2364, Test Accuracy: 30.29%
Coarse label:  1
Batch size:  64
Epoch 1/1, Loss: 3.6277, Accuracy: 26.36%
EVALUATING FINE MODEL
Test Loss: 2.2325, Test Accuracy: 33.71%
Coarse label:  2
Batch size:  64
Epoch 1/1, Loss: 3.8501, Accuracy: 23.61%
EVALUATING FINE MODEL
Test Loss: 2.2922, Test Accuracy: 32.14%
Coarse label:  3
Batch size:  64
E

In [217]:
def relabel_data_with_label_dict(coarse_model, fine_models, dataset, label_dictionary, strikes=1, threshold=-0.5, device='cpu'):
    """
    Relabel the dataset using the coarse model, fine models, and label dictionary.

    Args:
        coarse_model (torch.nn.Module): The coarse model for coarse label predictions.
        fine_models (dict): A dictionary mapping coarse labels to fine-grained models.
                            e.g., {0: fine_model_for_coarse_0, 1: fine_model_for_coarse_1, ...}.
        dataset (torch.utils.data.Dataset): Original PyTorch dataset with samples as (data, original_coarse_label, original_fine_label).
        label_dictionary (dict): A dictionary mapping dataset samples to their respective coarse and fine labels.
                                 Format: {index: {'coarse_label': int, 'fine_label': int}, ...}.
        batch_size (int): Batch size for processing the data.
        device (str): Device to use ('cpu' or 'cuda').

    Returns:
        List[Tuple[Tensor, int, int]]: A list of tuples (data, new_coarse_label, new_fine_label).

    Strategy:
    1. Coarse Model Prediction:
      The coarse model predicts the coarse label and its confidence.

    2. Selecting the Fine Model:
      Use the predicted coarse label to select the corresponding fine model from fine_models.
      Fine Model Confidence Comparison:

    3. Predict the fine label and confidence using the selected fine model.
      Compare this confidence with the confidence of the provided fine label in label_dictionary.
      Relabel based on the higher confidence.
    4. Fallback Handling:
      If no fine model exists for the predicted coarse label, the function retains the original fine label.

    #Check if the coarse and fine label match the predictions, if so just add them without any changes.
    #update the global dictionary with the new label.
    #update the global dictionary with the new coarse label (there's a fine-coarse dictionary)
    """


    # Move models to the specified device
    coarse_m = coarse_model['model']
    coarse_m = coarse_m.to(device).eval()
    fine_ms = {k: model['model'].to(device).eval() for k, model in fine_models.items()}

    # Create DataLoader for the dataset
    # dataloader = DataLoader(dataset, batch_size=1, shuffle=False)
    # dataloader = dataloader.to(device)
    relabeled_data = []


    # Iterate through the dataset
    with torch.no_grad():
        # for batch_idx, (data, _) in enumerate(dataloader):
        # data = data.to(device)  # Move data to device
        # dataset = dataset.to(device)    

        for sample in dataset:
            # Predict coarse labels and confidence using coarse model
            image = sample[0]


            # print(sample[0].shape)  
            image = image.unsqueeze(0)
            image = image.to(device) 
            # print(sample[0].shape)
            # print(image.shape)

            coarse_outputs = coarse_m(image)  # Process one sample
            coarse_probs = torch.softmax(coarse_outputs, dim=1)
            coarse_conf, coarse_preds = torch.max(coarse_probs, dim=1)
            # print("coarse_preds: ", coarse_preds)
            # print("coarse_conf: ", coarse_conf)
            coarse_conf = coarse_conf.item()
            coarse_pred = coarse_preds.item()

            # print("coarse_preds: ", coarse_preds)
            # print("coarse_conf: ", coarse_conf)

            # print("corase_preds: ", len(coarse_preds))
            # Iterate over individual samples in the batch
            # for i, coarse_pred in enumerate(coarse_preds):
            # data_idx = batch_idx * batch_size + i  # Find the corresponding index in the dataset

            # Fetch true labels and relevant fine model
            # true_coarse_label = label_dictionary[data_idx]['coarse_label']
            # true_fine_label = label_dictionary[data_idx]['fine_label']

            dataset_coarse_label = label_dictionary[sample[0]]['coarse_label']
            dataset_fine_label = label_dictionary[sample[0]]['fine_label']

            # print("DATASET COARSE LABEL: ", dataset_coarse_label)
            # print("DATASET FINE LABEL: ", dataset_fine_label)
            # print(coarse_fine_local_mapping[dataset_coarse_label].keys())
            # print(coarse_fine_local_mapping.keys())
            dataset_fine_local_label = coarse_fine_local_mapping[dataset_coarse_label][dataset_fine_label]



            # Use the predicted coarse label to select the corresponding fine model from fine_models.
            fine_model = fine_ms.get(coarse_pred, None)
            if fine_model:
                # Predict fine label using the fine model for the coarse prediction
                fine_outputs = fine_model(image)  # Process one sample
                fine_probs = torch.softmax(fine_outputs, dim=1)
                fine_conf, fine_pred = torch.max(fine_probs, dim=1)
                fine_conf = fine_conf.item()
                fine_pred = fine_pred.item()
                temp1 = coarse_fine_local_mapping[coarse_pred]
                fine_pred_label_global = [k for k, v in temp1.items() if v == fine_pred][0]
                # fine_pred_label_global = coarse_fine_local_mapping[coarse_pred][fine_pred]

            # print("FINE PREDICTION: ", fine_pred_label_global, " - ",fine_labels_string[fine_pred_label_global], "  Confidence: ", fine_conf)

            # Get the fine model coresponding to the coarse label we have in the dataset
            fine_model_ds_label = fine_ms.get(dataset_coarse_label, None)
            if fine_model_ds_label:
                # Compare fine model confidence with the confidence of the true fine label
                # true_fine_conf = fine_probs[0, true_fine_label].item()
                fine_outputs_dataset = fine_model_ds_label(image)
                fine_probs_dataset = torch.softmax(fine_outputs_dataset, dim=1)
                fine_conf_dataset = fine_probs_dataset[:, dataset_fine_local_label]                
                fine_conf_dataset = fine_conf_dataset.item()
                # temp2 = coarse_fine_local_mapping[dataset_coarse_label]
                fine_pred_label_global_dataset =  dataset_fine_label #[k for k, v in temp2.items() if v == dataset_fine_local_label][0]
                # fine_pred_label_global_dataset = coarse_fine_local_mapping[dataset_coarse_label][fine_pred_dataset]

            # print("FINE PREDICTION DATASET: ", fine_pred_label_global_dataset, " - ",fine_labels_string[fine_pred_label_global_dataset], "  Confidence: ", fine_conf_dataset)

            # print("Conf: ", fine_conf, " - ", "threshold: ", threshold) 
            if fine_model and fine_model_ds_label:
                if fine_conf> fine_conf_dataset and fine_pred_label_global != -1 and fine_pred_label_global != fine_pred_label_global_dataset and fine_conf > threshold:

                    #print("STRIKE! Pred Class: ", fine_pred_label_global, " - ",fine_labels_string[fine_pred_label_global], "  Confidence: ", fine_conf, "  |  Dataset Class: ", fine_pred_label_global_dataset," - ", fine_labels_string[fine_pred_label_global_dataset], "  Confidence: ", fine_conf_dataset)

                    fine_label_pred = fine_pred_label_global  # Use the fine model's prediction
                    
                    if label_dictionary[sample[0]]['last_predicted'] == fine_label_pred:
                        label_dictionary[sample[0]]['last_predicted_count'] += 1
                        # print("STRIKE COUNT: ", label_dictionary[sample[0]]['last_predicted_count'])
                    else:
                        label_dictionary[sample[0]]['last_predicted'] = fine_label_pred
                        label_dictionary[sample[0]]['last_predicted_count'] = 1
                        # print("Sample:,", fine_label_pred, ",STRIKE COUNT: ", label_dictionary[sample[0]]['last_predicted_count'])
                # relabeled_data.append(sample[0], new_fine_label)

            # print(len(fine_labels_string))

            if label_dictionary[sample[0]]['last_predicted_count'] >= strikes:
                print("RELABELELD! Previous Class: ", label_dictionary[sample[0]]['fine_label'], " - ",fine_labels_string[label_dictionary[sample[0]]['fine_label']],  "  New Class: ", label_dictionary[sample[0]]['last_predicted'], " - ",fine_labels_string[label_dictionary[sample[0]]['last_predicted']])
                label_dictionary[sample[0]]['fine_label'] = label_dictionary[sample[0]]['last_predicted']
                label_dictionary[sample[0]]['coarse_label'] = fine_to_coarse_mapping[label_dictionary[sample[0]]['last_predicted']]
                label_dictionary[sample[0]]['last_predicted'] = -1
                label_dictionary[sample[0]]['last_predicted_count'] = 0
                label_dictionary[sample[0]]['has_flipped'] = 1
                
            # Update the coarse label if the prediction differs from the true coarse label

In [244]:
# Apply asymmetric noise to the dataset
def apply_asymmetric_noise(dataset,label_dictionary, noise_rate=0.1):
    """
    Apply asymmetric noise to the dataset. Increment the label by 1 and wrap around if noise is applied.
    """
    noisy_dataset = []
    new_fine = -10
    for data, fine in dataset:
        if random.random() < noise_rate:
            # print("LABEL1 DICTIONARY:",label_dictionary[data])
            label_dictionary[data]['should_flip'] = 1
            # print("LABEL2 DICTIONARY:",label_dictionary[data])
            new_fine = (fine + 1) % len(fine_labels)  # Increment label cyclically
            label_dictionary[data]['fine_label'] = new_fine
            # print("LABEL3 DICTIONARY:",label_dictionary[data])
            label_dictionary[data]['coarse_label'] = fine_to_coarse_mapping[new_fine]  # Get the new coarse label
            # print("LABEL4 DICTIONARY:",label_dictionary[data])
        noisy_dataset.append((data, label_dictionary[data]['fine_label']))
    return noisy_dataset, label_dictionary


# Apply symmetric noise to the dataset
def apply_symmetric_noise(dataset,label_dictionary, noise_rate=0.1):
    """
    Apply symmetric noise to the dataset. Randomly replace the label with any other label.
    """
    noisy_dataset = []
    new_fine = -10
    for data, fine in dataset:
        if random.random() < noise_rate:
            # print("LABEL1 DICTIONARY:",label_dictionary[data])
            label_dictionary[data]['should_flip'] = 1
            # print("LABEL2 DICTIONARY:",label_dictionary[data])
            new_fine = random.choice(list(fine_to_coarse_mapping.keys()))  # Randomly choose a new label
            label_dictionary[data]['fine_label'] = new_fine
            # print("LABEL3 DICTIONARY:",label_dictionary[data])
            label_dictionary[data]['coarse_label'] = fine_to_coarse_mapping[new_fine]  # Get the new coarse label
            # print("LABEL4 DICTIONARY:",label_dictionary[data])
        noisy_dataset.append((data, label_dictionary[data]['fine_label']))
    return noisy_dataset, label_dictionary

# test1 = apply_asymmetric_noise(cifar100_coarse_dataset, noise_rate=0.1)

In [245]:
def get_confusion_matrix(dataset, lbl_dict):
    TP_fine = 0
    TN_fine = 0
    FP_fine = 0
    FN_fine = 0

    TP_coarse = 0
    TN_coarse = 0
    FP_coarse = 0
    FN_coarse = 0

    for sample in dataset:
        image = sample[0]
        # print("TN_fine: ", TN_fine, "TP_fine: ", TP_fine, "FP_fine: ", FP_fine, "FN_fine: ", FN_fine)
        # print("TN_coarse: ", TN_coarse, "TP_coarse: ", TP_coarse, "FP_coarse: ", FP_coarse, "FN_coarse: ", FN_coarse)
        # print("should flip: ", lbl_dict[image]['should_flip'])
        # print("fine label: ", lbl_dict[image]['fine_label'])
        # print("coarse label: ", lbl_dict[image]['coarse_label'])
        # print("original fine label: ", lbl_dict[image]['original_fine'])
        # print("original coarse label: ", lbl_dict[image]['original_coarse'])


        if lbl_dict[image]['coarse_label'] == lbl_dict[image]['original_coarse'] and lbl_dict[image]['should_flip'] == 1 and lbl_dict[image]['has_flipped'] == 1:
            TP_coarse += 1
        elif lbl_dict[image]['coarse_label'] != lbl_dict[image]['original_coarse'] and lbl_dict[image]['should_flip'] == 1:
            FN_coarse += 1
        elif lbl_dict[image]['coarse_label'] == lbl_dict[image]['original_coarse'] and lbl_dict[image]['should_flip'] == 0 and lbl_dict[image]['has_flipped'] == 0:
            TN_coarse += 1
        elif lbl_dict[image]['coarse_label'] != lbl_dict[image]['original_coarse'] and lbl_dict[image]['should_flip'] == 0 and lbl_dict[image]['has_flipped'] == 1:
            FP_coarse += 1
    
        if lbl_dict[image]['fine_label'] == lbl_dict[image]['original_fine'] and lbl_dict[image]['should_flip'] == 1 and lbl_dict[image]['has_flipped'] == 1:
            TP_fine += 1
        elif lbl_dict[image]['fine_label'] != lbl_dict[image]['original_fine'] and lbl_dict[image]['should_flip'] == 1:
            FN_fine += 1
        elif lbl_dict[image]['fine_label'] == lbl_dict[image]['original_fine'] and lbl_dict[image]['should_flip'] == 0:
            TN_fine += 1
        elif lbl_dict[image]['fine_label'] != lbl_dict[image]['original_fine'] and lbl_dict[image]['should_flip'] == 0 and lbl_dict[image]['has_flipped'] == 1:
            FP_fine += 1

        # print("TN_fine: ", TN_fine, "TP_fine: ", TP_fine, "FP_fine: ", FP_fine, "FN_fine: ", FN_fine)
        # print("TN_coarse: ", TN_coarse, "TP_coarse: ", TP_coarse, "FP_coarse: ", FP_coarse, "FN_coarse: ", FN_coarse)
        # print('------------------------------------------------')

    return TP_fine, TN_fine, FP_fine, FN_fine, TP_coarse, TN_coarse, FP_coarse, FN_coarse

In [246]:
def generate_dataset_from_label_dict(label_dict):
    new_dataset = []
    for sample in label_dict.keys():
        new_dataset.append((sample, label_dict[sample]['fine_label']))
    return new_dataset

In [257]:

### BIG RUN ###

# Select noise type

relabel_steps =2
threshold = 0.85
# strikes = 1
label_dictionary = {}
metric_dict = {}

### We need to run over the following combinations of parameters: strikes [1,2,3], threshold [0.3, 0.5, 0.8], relabel_steps [1,2,3]
for strikes in [2,1,3]:
    metric_dict[strikes] = {}
    for noise_type in ['asymmetric', 'symmetric']:
        metric_dict[strikes][noise_type] = {}
        # Select noise rate
        for noise in [0.1, 0, 0.2, 0.3]:
            metric_dict[strikes][noise_type][noise] = {}
            # Load the CIFAR-100 dataset - CLEAN VERSION

            # i = 0
            # cifar100_coarse_dataset = []
            # for data in cifar100_all:
            #     i+=1
            #     if i == 1000:
            #         break
            #     processd = preprocess_data(data)
            #     cifar100_coarse_dataset.append(processd)


            cifar100_coarse_dataset = [
                preprocess_data(data) for data in cifar100_all
            ]

            
            # Create a dictionary to store the labels and metadata for each sample
            label_dictionary = {}
            for sample in cifar100_coarse_dataset:
                coarse_lbl = deepcopy(fine_to_coarse_mapping[sample[1]])
                label_dictionary[sample[0]] = {'coarse_label':deepcopy(coarse_lbl), 'fine_label':deepcopy(sample[1]), 'original_coarse':deepcopy(coarse_lbl), 'original_fine':deepcopy(sample[1]), 'last_predicted':-1, 'last_predicted_count':0, 'should_flip':0, 'has_flipped':0}





            # Remove metadata from the dataset
            # cifar100_coarse_dataset = [(sample[0], sample[1], sample[2]) for sample in cifar100_coarse_dataset]
            cifar_train, cifar_test = get_train_test(cifar100_coarse_dataset, train_split=0.9)

            # Apply noise to the coarse dataset if needed
            if noise > 0:
                if noise_type == 'symmetric':
                    cifar_train, label_dictionary = apply_symmetric_noise(cifar_train,label_dictionary, noise_rate=noise)
                else:
                    cifar_train, label_dictionary = apply_asymmetric_noise(cifar_train,label_dictionary, noise_rate=noise)


            # print(sum([1 for sample in cifar_train if label_dictionary[sample[0]]['should_flip'] == 1]))

            # print(sum([1 for sample in cifar_train]))

            # print(sum([1 for sample in label_dictionary.keys() if label_dictionary[sample]['should_flip'] == 1]))

            # TP_fine, TN_fine, FP_fine, FN_fine, TP_coarse, TN_coarse, FP_coarse, FN_coarse = get_confusion_matrix(cifar_train, label_dictionary)
            # print("CONFUSION MATRIX: ")
            # print("TP_fine: ", TP_fine, "  TN_fine: ", TN_fine, "  FP_fine: ", FP_fine, "  FN_fine: ", FN_fine)
            # print("TP_coarse: ", TP_coarse, "  TN_coarse: ", TN_coarse, "  FP_coarse: ", FP_coarse, "  FN_coarse: ", FN_coarse)

            # Map coarse_train and coarse_test to retain only (data, coarse) tuples
            coarse_train = [(data, fine_to_coarse_mapping[fine]) for data, fine in cifar_train]
            coarse_test = [(data, fine_to_coarse_mapping[fine]) for data, fine in cifar_test]

            # cifar100_coarse_dataset = [(sample[0], sample[2]) for sample in cifar100_coarse_dataset]


            fine_datasets, coarse_fine_local_mapping = get_fine_datasets_and_mappings(cifar_train, coarse_labels)
            fine_datasets_test, _ = get_fine_datasets_and_mappings(cifar_test, coarse_labels, mapping=coarse_fine_local_mapping)



            for coarse_label in coarse_to_fine_mapping.keys():
                # Split fine-grained dataset for this coarse label
                # fine_train, fine_test = get_train_test(fine_datasets[coarse_label],train_split=0.9)
                fine_train, fine_test = fine_datasets[coarse_label], fine_datasets_test[coarse_label]

                # Modify fine_train to remove relevant labels
                fine_training_datasets[coarse_label] = [
                    (data, fine) for data, fine in fine_train
                ]

                # if noise > 0:
                #     if noise_type == 'symmetric':
                #         fine_training_datasets[coarse_label] = apply_symmetric_noise(fine_training_datasets[coarse_label], label_dictionary, noise_rate=noise)
                #     else:
                #         fine_training_datasets[coarse_label] = apply_asymmetric_noise(fine_training_datasets[coarse_label], label_dictionary, noise_rate=noise)


                # Store the testing dataset
                fine_testing_datasets[coarse_label] = [
                    (data, fine) for data, fine in fine_test
                ]

                # print(len(fine_training_datasets[coarse_label]))





            print("NOISE: ", noise, "  NOISE TYPE: ", noise_type)
            final_run = False

            # final_acc_training_coarse = []
            # final_acc_training_fine = []
            # final_acc_testing_coarse = []
            # final_acc_testing_fine = []

            # final_accuracy_fine = []
            # final_accuracy_coarse = []
            # final_precision_fine = []
            # final_precision_coarse = []

            relable_step_accuracy_training_coarse = []
            relabel_step_fine_metrics = []
            relable_step_accuracy_testing_coarse = []

            for i in range(relabel_steps+1):
                metric_dict[strikes][noise_type][noise][i] = {} 

                if i == relabel_steps:
                    final_run = True
                
                if final_run:
                    print("FINAL RUN!")
                else:
                    print("RELABEL STEP: ", i)


                

                # Get fine datasets and local mappings
                # uniq_coarse_labels = set(sample[1] for sample in coarse_train)

                # print("SUAN:", uniq_coarse_labels)

                fine_datast = [(sample[0], label_dictionary[sample[0]]['fine_label']) for sample in coarse_train]
                # uniq_coarse_labels = set(sample[1] for sample in fine_datast)
                # print("SONRA:", uniq_coarse_labels)

                fine_datasets, coarse_fine_local_mapping = get_fine_datasets_and_mappings(fine_datast, coarse_labels)

                for coarse_label in coarse_to_fine_mapping.keys():
                    fine_train = fine_datasets[coarse_label]

                    # Modify fine_train to remove relevant labels
                    fine_training_datasets[coarse_label] = [
                        (data, fine) for data, fine in fine_train
                    ]


                # Split the coarse dataset into training and testing subsets
                # coarse_train, coarse_test = get_train_test(cifar100_coarse_dataset)



                # Split the fine datasets into training and testing subsets



                    
                # Create the Bayesian model for coarse classification
                model_cifar100_coarse = BayesianModel(num_classes=20)  # 20 coarse classes
                model_cifar100_coarse.train()
                # model_cifar100_coarse = DeterministicModel(num_classes=20)  # Replace with a smaller architecture if needed

                # Define optimizer and loss function for the coarse model
                coarse_optimizer = optim.Adam(model_cifar100_coarse.parameters(), lr=0.001)
                coarse_loss_fn = nn.CrossEntropyLoss()  # Similar to sparse_categorical_crossentropy in TensorFlow

                coarse_model = {
                    'model': model_cifar100_coarse,
                    'optimizer': coarse_optimizer,
                    'loss_fn': coarse_loss_fn
                }
                
                
                # Set training parameters
                BATCH_SIZE = 128
                EPOCHS = 30 if not final_run else 45
                kl_weight = 0.001


                # unq_coarse_labels = set(sample[1] for sample in coarse_train)
                # print("UNIQUE COARSE LABELS: ", unq_coarse_labels)

                coarse_train = [(sample[0], label_dictionary[sample[0]]['coarse_label']) for sample in coarse_train]
                train_loader = DataLoader(coarse_train, batch_size=BATCH_SIZE, shuffle=True)
                # Train the coarse model
                coarse_accuracy, coarse_loss = train_model_with_kl(coarse_model['model'], train_loader, coarse_model['optimizer'], coarse_model['loss_fn'], kl_weight, EPOCHS)
                coarse_eval_avg_loss, coarse_eval_accuracy = evaluate_model(coarse_model['model'], coarse_model['loss_fn'], coarse_test, batch_size=128)
                # print("EVALUATING COARSE MODEL")
                # print("Accuracy: ", coarse_eval_accuracy, "  Loss: ", coarse_eval_avg_loss)


                # Create fine-grained models for each coarse label
                fine_models = {}

                fine_model_metrics = {}

                print("Training Fine Models...")
                for coarse_label, fine_labels in coarse_to_fine_mapping.items():

                    # Number of classes for this fine-grained model (including the no_match class)
                    no_classes = len(fine_labels) + 1  # Add 1 for the no_match label

                    # Create a small Bayesian model for fine-grained classification
                    fine_model = SmallBayesianModel(num_classes=no_classes)  # Replace with a smaller architecture if needed
                    # fine_model = SmallDeterministicModel(num_classes=no_classes)  # Replace with a smaller architecture if needed
                    # fine_model = BayesianModel(num_classes=no_classes)  # Replace with a smaller architecture if needed
                    # Define optimizer and loss function for the fine-grained model
                    fine_optimizer = optim.Adam(fine_model.parameters(), lr=0.001)
                    fine_loss_fn = nn.CrossEntropyLoss()

                    fine_models[coarse_label] = {
                        'model': fine_model,
                        'optimizer': fine_optimizer,
                        'loss_fn': fine_loss_fn
                    }

                # Train the fine-grained models
                EPOCHS = 40 if not final_run else 60
                kl_weight = 0.001
                
                for coarse_label, fine_labels in coarse_to_fine_mapping.items():
                    BATCH_SIZE = 128
                    fine_dataset_local = DataLoader(fine_training_datasets[coarse_label], batch_size=BATCH_SIZE, shuffle=True)
                    fine_model = fine_models[coarse_label]
                    fine_model['model'].train()

                    acc, loss = train_model_with_kl(fine_model['model'], fine_dataset_local, fine_model['optimizer'], fine_model['loss_fn'], kl_weight, EPOCHS)
                    eval_loss_fine, eval_acc_fine = evaluate_model(fine_model['model'], fine_model['loss_fn'], fine_testing_datasets[coarse_label], batch_size=128)
                    # print("EVALUATING FINE MODEL")
                    # print("Accuracy: ", eval_acc_fine, "  Loss: ", eval_loss_fine)

                    fine_model_metrics[coarse_label] = {'accuracy': acc, 'loss': loss}
                    fine_model_metrics[coarse_label]['eval_accuracy'] = eval_acc_fine
                    fine_model_metrics[coarse_label]['eval_loss'] = eval_loss_fine
                
                relabel_data_with_label_dict(coarse_model, fine_models, coarse_train, label_dictionary, strikes=strikes, threshold=threshold, device=device)
                coarse_train = generate_dataset_from_label_dict(label_dictionary)
                
                TP_fine, TN_fine, FP_fine, FN_fine, TP_coarse, TN_coarse, FP_coarse, FN_coarse = get_confusion_matrix(coarse_train, label_dictionary)
                print("TP_fine: ", TP_fine, "TN_fine: ", TN_fine, "FP_fine: ", FP_fine, "FN_fine: ", FN_fine)
                print("TP_coarse: ", TP_coarse, "TN_coarse: ", TN_coarse, "FP_coarse: ", FP_coarse, "FN_coarse: ", FN_coarse)
                # print("ACCURACY FINE: ", (TP_fine + TN_fine)/(TP_fine + TN_fine + FP_fine + FN_fine))
                # print("ACCURACY COARSE: ", (TP_coarse + TN_coarse)/(TP_coarse + TN_coarse + FP_coarse + FN_coarse))
                # print("PRECISION FINE: ", TP_fine/(TP_fine + FP_fine))
                # print("PRECISION COARSE: ", TP_coarse/(TP_coarse + FP_coarse))
                # print("RECALL FINE: ", TP_fine/(TP_fine + FN_fine))
                # print("RECALL COARSE: ", TP_coarse/(TP_coarse + FN_coarse))
                # print("F1 FINE: ", 2*TP_fine/(2*TP_fine + FP_fine + FN_fine))
                # print("F1 COARSE: ", 2*TP_coarse/(2*TP_coarse + FP_coarse + FN_coarse))

                metric_dict[strikes][noise_type][noise][i]['TP_fine'] = TP_fine
                metric_dict[strikes][noise_type][noise][i]['TN_fine'] = TN_fine
                metric_dict[strikes][noise_type][noise][i]['FP_fine'] = FP_fine
                metric_dict[strikes][noise_type][noise][i]['FN_fine'] = FN_fine
                metric_dict[strikes][noise_type][noise][i]['TP_coarse'] = TP_coarse
                metric_dict[strikes][noise_type][noise][i]['TN_coarse'] = TN_coarse
                metric_dict[strikes][noise_type][noise][i]['FP_coarse'] = FP_coarse
                metric_dict[strikes][noise_type][noise][i]['FN_coarse'] = FN_coarse

                metric_dict[strikes][noise_type][noise][i]['acc_testing_coarse'] = coarse_eval_accuracy
                metric_dict[strikes][noise_type][noise][i]['acc_training_coarse'] = coarse_accuracy
                metric_dict[strikes][noise_type][noise][i]['fine_metrics'] = fine_model_metrics

                if coarse_model:
                    del coarse_model
                if fine_models:
                    del fine_models
                if fine_datasets:
                    del fine_datasets
                try:
                    del cifar100_coarse_dataset
                except NameError:
                    pass # not defined or already deleted
                #if cifar100_coarse_dataset:
                #    del cifar100_coarse_dataset
                try:
                    del cifar_train
                except NameError:
                    pass
                #if cifar_train:
                #    del cifar_train
                torch.cuda.empty_cache()  # Clears the memory cache for reallocation

            # Relabel the dataset using the models



NOISE:  0.1   NOISE TYPE:  asymmetric
RELABEL STEP:  0
Epoch 1/30, Loss: 2.9238, Accuracy: 13.96%
Epoch 2/30, Loss: 2.5692, Accuracy: 22.11%
Epoch 3/30, Loss: 2.4335, Accuracy: 26.84%
Epoch 4/30, Loss: 2.3303, Accuracy: 29.93%
Epoch 5/30, Loss: 2.2396, Accuracy: 32.72%
Epoch 6/30, Loss: 2.1504, Accuracy: 35.35%
Epoch 7/30, Loss: 2.0755, Accuracy: 37.68%
Epoch 8/30, Loss: 2.0067, Accuracy: 39.87%
Epoch 9/30, Loss: 1.9285, Accuracy: 42.22%
Epoch 10/30, Loss: 1.8470, Accuracy: 44.34%
Epoch 11/30, Loss: 1.7689, Accuracy: 46.79%
Epoch 12/30, Loss: 1.6910, Accuracy: 49.12%
Epoch 13/30, Loss: 1.6051, Accuracy: 51.29%
Epoch 14/30, Loss: 1.5153, Accuracy: 54.03%
Epoch 15/30, Loss: 1.4288, Accuracy: 56.51%
Epoch 16/30, Loss: 1.3396, Accuracy: 58.94%
Epoch 17/30, Loss: 1.2610, Accuracy: 61.07%
Epoch 18/30, Loss: 1.1713, Accuracy: 63.40%
Epoch 19/30, Loss: 1.0925, Accuracy: 66.06%
Epoch 20/30, Loss: 1.0049, Accuracy: 68.58%
Epoch 21/30, Loss: 0.9317, Accuracy: 70.67%
Epoch 22/30, Loss: 0.8609, Acc

In [259]:
import json

#metric_dict
# Save list to a JSON file
with open("metric_dict.json", "w") as file:
    json.dump(metric_dict, file)

## Results

The `metric_dict` is a nested dictionary that stores performance metrics for a variety of conditions, including:

```metric_dict[strikes][noise_type][noise][i] = {
    # Confusion matrix metrics
    'TP_fine': ..., 'TN_fine': ..., 'FP_fine': ..., 'FN_fine': ...,
    'TP_coarse': ..., 'TN_coarse': ..., 'FP_coarse': ..., 'FN_coarse': ...,
    
    # Accuracy metrics
    'acc_testing_coarse': ...,
    'acc_training_coarse': ...,
    'fine_metrics': {...}  # Contains per-coarse-label metrics
}
```

The dictionary has a 4-level nested structure:

```strikes: [1, 2, 3]
noise_type: ['asymmetric', 'symmetric']
noise: [0, 0.1, 0.2, 0.3]
relabel_steps: [0 to relabel_steps]
```

In [ ]:
import pandas as pd
import seaborn as sns
import matplotlib.pyplot as plt
import numpy as np
from matplotlib.gridspec import GridSpec

def convert_metrics_to_df(metric_dict):
    """Convert nested metric_dict to a pandas DataFrame with proper error handling"""
    rows = []
    for strikes in metric_dict.keys():
        for noise_type in metric_dict[strikes].keys():
            for noise in metric_dict[strikes][noise_type].keys():
                for step in metric_dict[strikes][noise_type][noise].keys():
                    metrics = metric_dict[strikes][noise_type][noise][step]
                    
                    # Safely extract scalar values
                    acc_test = metrics['acc_testing_coarse']
                    acc_train = metrics['acc_training_coarse']
                    
                    # Handle potential list/array values by taking mean if necessary
                    acc_test = np.mean(acc_test) if isinstance(acc_test, (list, np.ndarray)) else acc_test
                    acc_train = np.mean(acc_train) if isinstance(acc_train, (list, np.ndarray)) else acc_train
                    
                    # Calculate metrics with error handling
                    try:
                        accuracy_fine = (metrics['TP_fine'] + metrics['TN_fine']) / max(1e-10, 
                            metrics['TP_fine'] + metrics['TN_fine'] + 
                            metrics['FP_fine'] + metrics['FN_fine'])
                        
                        accuracy_coarse = (metrics['TP_coarse'] + metrics['TN_coarse']) / max(1e-10,
                            metrics['TP_coarse'] + metrics['TN_coarse'] + 
                            metrics['FP_coarse'] + metrics['FN_coarse'])
                        
                        precision_fine = metrics['TP_fine'] / max(1e-10, metrics['TP_fine'] + metrics['FP_fine'])
                        recall_fine = metrics['TP_fine'] / max(1e-10, metrics['TP_fine'] + metrics['FN_fine'])
                        f1_fine = 2 * (precision_fine * recall_fine) / max(1e-10, precision_fine + recall_fine)
                        
                    except Exception as e:
                        print(f"Error calculating metrics: {e}")
                        continue
                    
                    row = {
                        'strikes': strikes,
                        'noise_type': noise_type,
                        'noise_level': float(noise),
                        'relabel_step': int(step),
                        'accuracy_fine': float(accuracy_fine),
                        'accuracy_coarse': float(accuracy_coarse),
                        'acc_testing_coarse': float(acc_test),
                        'acc_training_coarse': float(acc_train),
                        'precision_fine': float(precision_fine),
                        'recall_fine': float(recall_fine),
                        'f1_fine': float(f1_fine)
                    }
                    rows.append(row)
    
    return pd.DataFrame(rows)


def set_paper_style():
    """Set publication-quality style for plots"""
    plt.style.use('seaborn-v0_8-paper')
    plt.rcParams['figure.dpi'] = 300
    plt.rcParams['font.size'] = 10
    plt.rcParams['axes.labelsize'] = 12
    plt.rcParams['axes.titlesize'] = 14
    plt.rcParams['legend.fontsize'] = 10

def create_research_plots(df):
    """Generate all plots for research paper and save them separately as PNGs"""
    set_paper_style()
    
    # Create figure with subplots
    fig = plt.figure(figsize=(20, 25))
    gs = GridSpec(5, 2, figure=fig)
    
    # 1. Accuracy vs Relabel Steps
    ax1 = fig.add_subplot(gs[0, :])
    for noise_type in df['noise_type'].unique():
        for noise_level in sorted(df['noise_level'].unique()):
            data = df[(df['noise_type'] == noise_type) & (df['noise_level'] == noise_level)]
            ax1.plot(data['relabel_step'], data['acc_testing_coarse'], 
                    marker='o', label=f'{noise_type} (noise={noise_level})')
    ax1.set_xlabel('Relabel Step')
    ax1.set_ylabel('Testing Accuracy')
    ax1.set_title('(a) Accuracy Progression over Relabeling Steps')
    ax1.grid(True, alpha=0.3)
    ax1.legend(bbox_to_anchor=(1.05, 1), loc='upper left')
    # Save as PNG
    plt.savefig('accuracy_vs_relabel_steps.png', bbox_inches='tight')
    
    # 2. Confusion Matrix Heatmap
    ax2 = fig.add_subplot(gs[1, 0])
    pivot_data = df.pivot_table(
        values=['accuracy_fine', 'accuracy_coarse'],
        index=['noise_type', 'noise_level'],
        aggfunc='mean'
    )
    sns.heatmap(pivot_data, annot=True, cmap='YlOrRd', fmt='.3f', ax=ax2)
    ax2.set_title('(b) Fine vs Coarse Accuracy Comparison')
    # Save as PNG
    plt.savefig('confusion_matrix_heatmap.png', bbox_inches='tight')
    
    # 3. Learning Rate Analysis
    ax3 = fig.add_subplot(gs[1, 1])
    for noise_type in df['noise_type'].unique():
        data = df[df['noise_type'] == noise_type].groupby('relabel_step')['acc_testing_coarse'].mean()
        ax3.plot(data.index, data.values, marker='o', label=noise_type)
    ax3.set_xlabel('Relabel Step')
    ax3.set_ylabel('Average Testing Accuracy')
    ax3.set_title('(c) Learning Rate Analysis')
    ax3.grid(True, alpha=0.3)
    ax3.legend()
    # Save as PNG
    plt.savefig('learning_rate_analysis.png', bbox_inches='tight')
    
    # 4. Noise Impact Analysis
    ax4 = fig.add_subplot(gs[2, 0])
    sns.boxplot(data=df, x='noise_level', y='accuracy_coarse', 
                hue='noise_type', ax=ax4)
    ax4.set_title('(d) Impact of Noise Levels on Accuracy')
    ax4.set_xlabel('Noise Level')
    ax4.set_ylabel('Coarse Accuracy')
    # Save as PNG
    plt.savefig('noise_impact_analysis.png', bbox_inches='tight')
    
    # 5. Strike Impact Analysis
    ax5 = fig.add_subplot(gs[2, 1])
    sns.boxplot(data=df, x='strikes', y='accuracy_coarse', 
                hue='noise_type', ax=ax5)
    ax5.set_title('(e) Impact of Strikes on Model Performance')
    ax5.set_xlabel('Number of Strikes')
    ax5.set_ylabel('Coarse Accuracy')
    # Save as PNG
    plt.savefig('strike_impact_analysis.png', bbox_inches='tight')
    
    # 6. Precision-Recall Analysis
    ax6 = fig.add_subplot(gs[3, 0])
    sns.scatterplot(data=df, x='precision_fine', y='recall_fine', 
                    hue='noise_type', size='noise_level', ax=ax6)
    ax6.set_title('(f) Precision-Recall Distribution')
    ax6.set_xlabel('Precision')
    ax6.set_ylabel('Recall')
    # Save as PNG
    plt.savefig('precision_recall_analysis.png', bbox_inches='tight')
    
    # 7. F1 Score Trends
    ax7 = fig.add_subplot(gs[3, 1])
    sns.lineplot(data=df, x='relabel_step', y='f1_fine', 
                 hue='noise_type', style='noise_level', ax=ax7)
    ax7.set_title('(g) F1 Score Evolution')
    ax7.set_xlabel('Relabel Step')
    ax7.set_ylabel('F1 Score')
    # Save as PNG
    plt.savefig('f1_score_trends.png', bbox_inches='tight')
    
    # 8. Training-Testing Correlation
    ax8 = fig.add_subplot(gs[4, :])
    scatter = ax8.scatter(df['acc_training_coarse'], df['acc_testing_coarse'], 
                         c=df['noise_level'], cmap='viridis')
    ax8.set_xlabel('Training Accuracy')
    ax8.set_ylabel('Testing Accuracy')
    ax8.set_title('(h) Training vs Testing Accuracy Correlation')
    plt.colorbar(scatter, ax=ax8, label='Noise Level')
    # Save as PNG
    plt.savefig('training_testing_correlation.png', bbox_inches='tight')
    
    plt.tight_layout()  # Adjust subplots for better layout
    plt.close()  # Close the figure to prevent it from displaying all at once

def generate_summary_statistics(df):
    """Generate summary statistics for the paper with proper handling of metrics"""
    
    # Calculate mean performance for each configuration
    performance_by_config = df.groupby(['noise_type', 'noise_level', 'strikes']).agg({
        'accuracy_coarse': ['mean', 'std'],
        'acc_testing_coarse': ['mean', 'std'],
        'precision_fine': 'mean',
        'recall_fine': 'mean',
        'f1_fine': 'mean'
    }).round(4)
    
    # Find best configuration based on testing accuracy
    best_config = df.loc[df['acc_testing_coarse'].idxmax()]
    
    # Calculate convergence metrics
    convergence = df.groupby('relabel_step').agg({
        'acc_testing_coarse': ['mean', 'std'],
        'accuracy_coarse': ['mean', 'std']
    }).round(4)
    
    # Strike effectiveness analysis
    strike_analysis = df.groupby(['strikes', 'noise_type']).agg({
        'acc_testing_coarse': ['mean', 'std'],
        'f1_fine': 'mean'
    }).round(4)
    
    return {
        'overall_performance': performance_by_config,
        'best_config': best_config,
        'convergence': convergence,
        'strike_analysis': strike_analysis
    }

def analyze_and_plot_metrics(metric_dict):
    """Main function to analyze metrics and generate plots"""
    # Convert to DataFrame
    df = convert_metrics_to_df(metric_dict)
    
    # Generate plots
    _ = create_research_plots(df)
    
    # Generate summary statistics
    return generate_summary_statistics(df)

    

# Generate all analyses
summary = analyze_and_plot_metrics(metric_dict)

# Print summary statistics
print("\nSummary Statistics:")
print("\nOverall Performance by Noise Type and Level:")
print(summary['overall_performance'])
print("\nBest Configuration Found:")
for key, value in summary['best_config'].items():
    print(f"{key}: {value}")